In [31]:
# Imports & Inits

from datetime import datetime
from datetime import timezone
import polars as pl
import os

from utils import two_point_calibration, average_bottle, plot_sensor_measurement


DATA_DIRECTORY = os.environ.get("DATA_DIRECTORY")
PICARRO_DATA_DIRECTORY = os.environ.get("PICARRO_DATA_DIRECTORY")

#------------
sensor_id = 13
#------------

df = pl.scan_parquet(os.path.join(DATA_DIRECTORY, "download", "acropolis.parquet")) \
    .filter(pl.col("system_name") == f"tum-esm-midcost-raspi-{sensor_id}") \
    .sort(pl.col("creation_timestamp")) \
    .filter(pl.col("gmp343_filtered") > 0.0) \
    .select(pl.col("creation_timestamp"),
                pl.col("gmp343_filtered"),
                pl.col("sht45_humidity"))
    

df_p = pl.scan_parquet(os.path.join(DATA_DIRECTORY, "input/picarro.parquet")) 

In [32]:
df.head(3).collect()

shape: (3, 3)
┌─────────────────────────────┬─────────────────┬────────────────┐
│ creation_timestamp          ┆ gmp343_filtered ┆ sht45_humidity │
│ ---                         ┆ ---             ┆ ---            │
│ datetime[μs, UTC]           ┆ f64             ┆ f64            │
╞═════════════════════════════╪═════════════════╪════════════════╡
│ 2023-08-02 14:58:22.920 UTC ┆ 553.5           ┆ 48.96          │
│ 2023-08-02 14:58:32.930 UTC ┆ 572.7           ┆ 48.99          │
│ 2023-08-02 14:58:42.940 UTC ┆ 546.4           ┆ 48.61          │
└─────────────────────────────┴─────────────────┴────────────────┘

# ICOS Calibration PICARRO

In [33]:
picarro_slope = 1.0060429925902534 
picarro_intercept = 0.09305508001614271

df_p.head(1).collect()

shape: (1, 27)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ DATE      ┆ TIME      ┆ FRAC_DAYS ┆ FRAC_HRS_ ┆ … ┆ wlm1_offs ┆ wlm2_offs ┆ datetime  ┆ __index_ │
│ ---       ┆ ---       ┆ _SINCE_JA ┆ SINCE_JAN ┆   ┆ et        ┆ et        ┆ ---       ┆ level_0_ │
│ str       ┆ str       ┆ N1        ┆ 1         ┆   ┆ ---       ┆ ---       ┆ datetime[ ┆ _        │
│           ┆           ┆ ---       ┆ ---       ┆   ┆ f64       ┆ f64       ┆ ns]       ┆ ---      │
│           ┆           ┆ f64       ┆ f64       ┆   ┆           ┆           ┆           ┆ i64      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ 2023-06-2 ┆ 00:00:01. ┆ 173.00001 ┆ 4152.0004 ┆ … ┆ -0.079042 ┆ -0.047342 ┆ 2023-06-2 ┆ 10662630 │
│ 3         ┆ 489       ┆ 7         ┆ 14        ┆   ┆           ┆           ┆ 3 00:00:0 ┆          │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆ 1.489     ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

# ICOS Calibration MC13 19.12.2023

In [34]:
# ---
# Measurement
# ---

#400
start_date = datetime(2023, 12, 19, 12, 5, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 12, 33, 0).replace(tzinfo=timezone.utc)

df_p_400 = df.sort("creation_timestamp").filter(pl.col("creation_timestamp").is_between(start_date, end_date))


#600
start_date = datetime(2023, 12, 19, 12, 34, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 13, 3, 0).replace(tzinfo=timezone.utc)

df_p_600 = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))



# ---
# Averagng
# ---

measured_values = [None, None]
true_values = [427.38, 610.95]

# 400 ppm

data = df_p_400.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
measured_values[0] = average_bottle(data)

# 600 ppm
data = df_p_600.select(pl.col("gmp343_filtered")).collect().to_series().to_list()

measured_values[1] = average_bottle(data)

# calculate slope and intercept
acropolis_slope, acropolis_intercept = two_point_calibration(measured_values, true_values)
print(f"acropolis_slope = {acropolis_slope}, acropolis_intercept = {acropolis_intercept}")

# plot
plot_sensor_measurement(df_p_400.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_p_400.collect(), col_name="sht45_humidity")
plot_sensor_measurement(df_p_600.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_p_600.collect(), col_name="sht45_humidity")


Uncut average: 451.31607142857155
Cut average: 451.3568807339451
Uncut average: 632.6536842105262
Cut average: 632.3838709677419
acropolis_slope = 1.0140476829610818, acropolis_intercept = -30.317399096798397


# Bottles on 19.12.2023

In [35]:
# bottle 41

# PICARRO
# 41		16:02	16:27	399,8
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 19, 14, 56, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 15, 21, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 19, 15, 29, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 15, 53, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 399.83020101048874
Cut average: 399.8277599852567
Picarro Average: 402.3369712562414
Starting ACROPOLIS Processing
Uncut average: 424.94946236559156
Cut average: 425.04262295081963
MC13 Average: 400.696087866181


In [36]:
# bottle 42

# PICARRO
# 42		16:32	16:53	401.7
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 19, 15, 28, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 15, 47, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 19, 15, 55, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 16, 15, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 401.7530479136656
Cut average: 401.7580719342861
Picarro Average: 404.2789480660756
Starting ACROPOLIS Processing
Uncut average: 426.9219178082193
Cut average: 426.8583333333332
MC13 Average: 402.53730477249724


In [37]:
# bottle 43

# PICARRO
# 43		16:55	17:15	401,5
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 19, 15, 51, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 16, 9, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 19, 16, 18, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 16, 40, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 401.5764390815291
Cut average: 401.57605375355604
Picarro Average: 404.09582995082815
Starting ACROPOLIS Processing
Uncut average: 426.4337209302325
Cut average: 426.3392857142855
MC13 Average: 402.01096573705547


In [38]:
# bottle 44

# PICARRO
# 44		17:18	17:40	401,7
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 19, 16, 14, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 16, 34, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 19, 16, 42, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 17, 2, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 401.6654835348614
Cut average: 401.6509016488742
Picarro Average: 404.1711301514231
Starting ACROPOLIS Processing
Uncut average: 426.2551282051283
Cut average: 426.2803921568629
MC13 Average: 401.9512448616097


In [39]:
# bottle 45

# PICARRO
# 45		17:41	18:02	403,6
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 19, 16, 36, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 16, 56, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 19, 17, 5, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 17, 24, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 403.73266815821967
Cut average: 403.7371890866802
Picarro Average: 406.2700250087569
Starting ACROPOLIS Processing
Uncut average: 428.6986486486486
Cut average: 428.7937499999998
MC13 Average: 404.4999095588948


In [40]:
# bottle 46

# PICARRO
# 46		18:04	18:24	403,2
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 19, 16, 59, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 17, 18, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 19, 17, 26, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 19, 17, 51, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 403.31663483871057
Cut average: 403.3121405492016
Picarro Average: 405.84240790611585
Starting ACROPOLIS Processing
Uncut average: 428.0670103092782
Cut average: 427.95873015873013
MC13 Average: 403.65315962362877


# ICOS Calibration MC13 20.12.2023

In [41]:

# ---
# Measurement
# ---

#400
start_date = datetime(2023, 12, 20, 12, 36, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 13, 11, 0).replace(tzinfo=timezone.utc)

df_p_400 = df.sort("creation_timestamp").filter(pl.col("creation_timestamp").is_between(start_date, end_date))


#600
start_date = datetime(2023, 12, 20, 13, 12, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 13, 42, 0).replace(tzinfo=timezone.utc)

df_p_600 = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))



# ---
# Averagng
# ---

measured_values = [None, None]
true_values = [427.38, 610.95]

# 400 ppm

data = df_p_400.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
measured_values[0] = average_bottle(data)

# 600 ppm
data = df_p_600.select(pl.col("gmp343_filtered")).collect().to_series().to_list()

measured_values[1] = average_bottle(data)

# calculate slope and intercept
acropolis_slope, acropolis_intercept = two_point_calibration(measured_values, true_values)
print(f"acropolis_slope = {acropolis_slope}, acropolis_intercept = {acropolis_intercept}")

# plot
plot_sensor_measurement(df_p_400.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_p_400.collect(), col_name="sht45_humidity")
plot_sensor_measurement(df_p_600.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_p_600.collect(), col_name="sht45_humidity")


Uncut average: 445.22740384615406
Cut average: 445.6111111111112
Uncut average: 628.603888888889
Cut average: 628.9863247863249
acropolis_slope = 1.001062228208941, acropolis_intercept = -18.704451803550967


In [42]:
# bottle 47

# PICARRO
# 47	20.12.2023	10:49	11:09	400,2
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 9, 43, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 3, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 11:10	11:30
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 10, 10, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 30, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 400.2430651865782
Cut average: 400.2518400391265
Picarro Average: 402.7636140227344
Starting ACROPOLIS Processing
Uncut average: 420.8421052631578
Cut average: 420.8000000000001
MC13 Average: 402.54253382677155


In [43]:
# bottle 48

# PICARRO
# 48		11:10	11:30	401,4
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 10, 5, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 24, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 11:31	11:51
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 10, 31, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 51, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 401.3283377840646
Cut average: 401.32542333651054
Picarro Average: 403.8436849760295
Starting ACROPOLIS Processing
Uncut average: 421.8435897435897
Cut average: 421.86274509803906
MC13 Average: 403.6064078026325


In [44]:
# bottle 49

# PICARRO  
# 49		11:31	11:51   401,3
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 10, 26, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 45, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 10, 31, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 51, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 401.483531410918
Cut average: 401.4866368929442
Picarro Average: 404.00587274479017
Starting ACROPOLIS Processing
Uncut average: 421.8435897435897
Cut average: 421.86274509803906
MC13 Average: 403.6064078026325


Corrected Picarro Timeshift on Windows PC

In [45]:
# bottle 50

# PICARRO
# 50		13:54	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 12, 45, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 45, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 10, 31, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 51, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Length of list to average is 0.
Picarro Average: 0.09305508001614271
Starting ACROPOLIS Processing
Uncut average: 421.8435897435897
Cut average: 421.86274509803906
MC13 Average: 403.6064078026325


In [46]:
# bottle 51

# PICARRO
# 51		14:15	14:35	399,9
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 13, 15, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 13, 35, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 10, 31, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 10, 51, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Length of list to average is 0.
Picarro Average: 0.09305508001614271
Starting ACROPOLIS Processing
Uncut average: 421.8435897435897
Cut average: 421.86274509803906
MC13 Average: 403.6064078026325


In [47]:
# bottle 52

# PICARRO
# 52		14:35	14:50	401,7
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 13, 15, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 13, 35, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 14:51	15:17
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 13, 56, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 14, 17, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Length of list to average is 0.
Picarro Average: 0.09305508001614271
Starting ACROPOLIS Processing
Uncut average: 424.89878048780474
Cut average: 424.9169811320754
MC13 Average: 406.66388813234096


In [48]:
# bottle 53

# PICARRO
# 53		14:57	15:17	401,4
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 13, 57, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 14, 17, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 15:19	15:39
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 14, 19, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 14, 39, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 405.65842361698225
Cut average: 407.24920042535916
Picarro Average: 409.8032594059324
Starting ACROPOLIS Processing
Uncut average: 424.8692307692306
Cut average: 424.83921568627454
MC13 Average: 406.5860400818899


In [49]:
# bottle 54

# PICARRO
# 54		15:19	15:39	401,1
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 13, 57, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 14, 17, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 15:40	16:00
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 14, 41, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 15, 0, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 405.65842361698225
Cut average: 407.24920042535916
Picarro Average: 409.8032594059324
Starting ACROPOLIS Processing
Uncut average: 424.76486486486493
Cut average: 424.8125
MC13 Average: 406.55929601745976


In [50]:
# bottle 55

# PICARRO
# 55		15:40	16:00	403,4
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 13, 57, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 14, 17, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 16:01	16:20
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 14, 41, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 15, 0, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 405.65842361698225
Cut average: 407.24920042535916
Picarro Average: 409.8032594059324
Starting ACROPOLIS Processing
Uncut average: 424.76486486486493
Cut average: 424.8125
MC13 Average: 406.55929601745976


In [51]:
# bottle 56

# PICARRO
# 56		16:01	16:20	401,4
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 20, 13, 57, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 14, 17, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# -- --
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 20, 14, 41, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 20, 15, 0, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 405.65842361698225
Cut average: 407.24920042535916
Picarro Average: 409.8032594059324
Starting ACROPOLIS Processing
Uncut average: 424.76486486486493
Cut average: 424.8125
MC13 Average: 406.55929601745976


# ICOS Calibration MC13 21.12.2023

In [52]:

# ---
# Measurement
# ---

#400
start_date = datetime(2023, 12, 21, 9, 21, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 9, 51, 0).replace(tzinfo=timezone.utc)

df_p_400 = df.sort("creation_timestamp").filter(pl.col("creation_timestamp").is_between(start_date, end_date))


#600
start_date = datetime(2023, 12, 21, 9, 51, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 10, 11, 0).replace(tzinfo=timezone.utc)

df_p_600 = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))



# ---
# Averagng
# ---

measured_values = [None, None]
true_values = [427.38, 610.95]

# 400 ppm

data = df_p_400.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
measured_values[0] = average_bottle(data)

# 600 ppm
data = df_p_600.select(pl.col("gmp343_filtered")).collect().to_series().to_list()

measured_values[1] = average_bottle(data)

# calculate slope and intercept
acropolis_slope, acropolis_intercept = two_point_calibration(measured_values, true_values)
print(f"acropolis_slope = {acropolis_slope}, acropolis_intercept = {acropolis_intercept}")

# plot
plot_sensor_measurement(df_p_400.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_p_400.collect(), col_name="sht45_humidity")
plot_sensor_measurement(df_p_600.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_p_600.collect(), col_name="sht45_humidity")


Uncut average: 447.7983050847457
Cut average: 447.23391304347814
Uncut average: 626.3058333333333
Cut average: 629.878205128205
acropolis_slope = 1.0050683648785683, acropolis_intercept = -22.120657700852405


In [53]:
# bottle 57

# PICARRO
# 57		10:24	10:44	403,3
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 9, 24, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 9, 44, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# -- --
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 14, 41, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 15, 0, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 432.9911707159671
Cut average: 432.95611485099187
Picarro Average: 435.66552052495746
Starting ACROPOLIS Processing
Uncut average: 547.8067567567564
Cut average: 547.7270833333333
MC13 Average: 528.3825063446882


In [54]:
# bottle 58

# PICARRO
# 58		10:45	11:05	403,1
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 9, 45, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 10, 5, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# -- --
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 14, 41, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 15, 0, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 432.5792187126426
Cut average: 432.54735380725657
Picarro Average: 435.2542893412637
Starting ACROPOLIS Processing
Uncut average: 547.8067567567564
Cut average: 547.7270833333333
MC13 Average: 528.3825063446882


In [55]:
# bottle 59

# PICARRO
# 59		11:06	11:26	401,4
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 10, 6, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 10, 26, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 11:27	11:47
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 10, 27, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 10, 47, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 468.6736318840002
Cut average: 488.65227026185187
Picarro Average: 491.6982473902709
Starting ACROPOLIS Processing
Uncut average: 425.10000000000014
Cut average: 425.1392156862746
MC13 Average: 405.1733186547086


In [56]:
# bottle 60

# PICARRO
# 60		11:27	11:47	403,1
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 10, 27, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 10, 47, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 11:48	12:08
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 10, 48, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 11, 8, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Uncut average: 407.4275380277248
Cut average: 409.4329107475292
Picarro Average: 412.00016587339854
Starting ACROPOLIS Processing
Uncut average: 426.9794871794871
Cut average: 426.9137254901962
MC13 Average: 406.95682232179706


In [ ]:
522.4 * picarro_slope + picarro_intercept

525.6499144091645

In [ ]:
# bottle 61

# PICARRO
# 61		11:48	12:08	522,4
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 10, 48, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 11, 8, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 13:26	13:46
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 12, 26, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 12, 46, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Length of list to average is 0.
Picarro Average: 0.09305508001614271
Starting ACROPOLIS Processing
Uncut average: 546.8089743589744
Cut average: 546.978431372549
MC13 Average: 527.6300599425997


In [ ]:
522.6 * picarro_slope + picarro_intercept

525.8511230076826

In [ ]:
# bottle 62

# PICARRO
# 62		13:26	13:46	522,6
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 12, 26, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 12, 46, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 13:48	14:08
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 12, 48, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 13, 8, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


Starting Picarro Processing
Length of list to average is 0.
Picarro Average: 0.09305508001614271
Starting ACROPOLIS Processing
Uncut average: 546.7820512820513
Cut average: 546.743137254902
MC13 Average: 527.3935732685106


In [ ]:
# bottle 63

# PICARRO
# 63		13:48	14:08	518,4
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 12, 48, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 13, 8, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 14:09	13:29
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 13, 9, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 13, 29, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 64

# PICARRO
# 64		14:09	14:29	522,3
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 13, 9, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 13, 29, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 14:30	14:50
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 13, 30, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 13, 50, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 65

# PICARRO
# 65		14:30	14:50	521,0	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 13, 30, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 13, 50, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 14:52	15:12
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 13, 52, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 14, 12, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 66

# PICARRO
# 66		14:52	15:12	520,7	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 13, 52, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 14, 12, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 15:13	15:33
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 14, 13, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 14, 33, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 67

# PICARRO
# 67		15:13	15:33	522,2	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 14, 13, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 14, 33, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 15:34	15:54
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 14, 34, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 14, 54, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 68

# PICARRO
# 68		15:34	15:54	522,5	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 14, 34, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 14, 54, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 15:55	16:15
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 14, 55, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 15, 15, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 69

# PICARRO
# 69		15:55	16:15	522,1	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 14, 55, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 15, 15, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 16:16	16:36
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 15, 16, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 15, 36, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 70

# PICARRO
# 70		16:16	16:36	521,7	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 15, 15, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 15, 36, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 16:37	17:00	
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 15, 37, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 16, 0, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")


In [ ]:
# bottle 71

# PICARRO
# 71		16:41	17:00	?	
print("Starting Picarro Processing")
start_date = datetime(2023, 12, 21, 15, 41, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 16, 0, 0).replace(tzinfo=timezone.utc)

df_p_bottle = df_p.select(pl.col("datetime").dt.cast_time_unit("us").dt.replace_time_zone("UTC").alias("creation_timestamp"),
            pl.col("CO2_dry"),
            pl.col("h2o_reported")) \
    .sort("creation_timestamp") \
    .filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_p_bottle.select(pl.col("CO2_dry")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * picarro_slope + picarro_intercept

print(f"Picarro Average: {avg}")

# ACROPOLIS
# 17:01	17:21
print("Starting ACROPOLIS Processing")
start_date = datetime(2023, 12, 21, 16, 1, 0).replace(tzinfo=timezone.utc)
end_date = datetime(2023, 12, 21, 16, 21, 0).replace(tzinfo=timezone.utc)

df_bottle = df.filter(pl.col("creation_timestamp").is_between(start_date, end_date))

data = df_bottle.select(pl.col("gmp343_filtered")).collect().to_series().to_list()
data_cut = data[int(len(data)*0.3):int(len(data)*0.95)]

avg = average_bottle(data_cut) * acropolis_slope + acropolis_intercept

print(f"MC13 Average: {avg}")


# Plots
plot_sensor_measurement(df_p_bottle.collect(), col_name="CO2_dry")
plot_sensor_measurement(df_p_bottle.collect(), col_name="h2o_reported")

plot_sensor_measurement(df_bottle.collect(), col_name="gmp343_filtered")
plot_sensor_measurement(df_bottle.collect(), col_name="sht45_humidity")
